## Modeling

### Table of Contents
- Introduction
- Import and Load Pre-processed Data
- SARIMA
- Evaluate SARIMA Models
- Advanced Modeling: Prophet
- Evaluate Prophet Models
- Final Conclusion / Findings

### Introduction
We have cleaned the initial database, performed EDA, and pre-processed the transformed dataset for modeling. Now it's the anticipated moment of modeling and forecasting. We will take a look at two models, SARIMA model as the baseline model and Meta (Facebook) Prophet model as the advanced model. Coming back to the question from the EDA of how the impact of COVID pandemic will affect the model forecasting. The baseline model and the advanced model will evaluate the entire dataset from Jan 2013 to May 2024 but also data before the pandemic, Jan 2013 to Jan 2020. It will be comparison of the baseline model against the advanced model but also a comparison of dataset with and without the pandemic impact. Essentially, which model performs better and how does the pandemic change the forecast. Let's begin.


### Import and Load Pre-processed Data

As we have always done, begin with importing the necessary libraries. We will load in the pre-processed and transformed dataset.

In [1]:
# import libraries
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import datetime as dt

In [3]:
# suppress Future Warnings
import warnings
warnings.simplefilter('ignore', category=FutureWarning)

In [2]:
# load in file and convert to datetime index
df_main = pd.read_csv('capstone_df_main.csv')
df_main['DATE'] = pd.to_datetime(df_main['DATE'])
df_main.set_index('DATE', inplace=True)

### SARIMA

During the pre-processing phase, we went through to find the parameters of SARIMA model (p,d,q)(P,D,Q,m). Order of AR (p) were either 1 or 2, order of differencing (d) was up to 3, order of MA were either (1 or 7), and the recurrent interval of seasonality was 12 months since our dataset is on a monthly basis.

Now the SARIMA model needs to be applied to each of the 61 destinations to forecast their passenger volume. To go through each of the 61 destinations and set up the parameters specific to each of the destinations would be inefficient and time consuming. Fortunately, there is the `auto_arima` function that will do the work for us.

A custom function `smodel` is created to utilize the `auto_arima` function to iterate through the destinations. As long as we have a range of the parameters, `auto_arima` function will perform a grid search to find the best parameters for each destination dataset. From the pre-processing phase, we saw how some destinations did not require differencing whereas others required one or more. The non-differentiated or base model will be inputted since the function will find the best order of differencing given a range.

In [4]:
from pmdarima.arima import auto_arima
def smodel(dataframe, dest, periods, cutoff, end=None):
    '''
    Description
    -----------
    Given a time series dataframe, the dataset will be splitted for train set and test set. 
    Using the train set, the auto_arima function with its range of parameters defined will perform a grid search to find the best parameters for a SARIMA model.
    The train set will be fitted with the best SARIMA model parameters then forecasted for the given number of periods.
    Train, test, and forecasted dataset along with the confidence interval will be returned.

    Inputs
    ------
    dataframe: dataframe of time series data
    dest: name of destination
    periods: timeframe to forecast
    cutoff: cutoff date for the train test split
    end (optional): ending date of the test set

    Outputs
    ------
    train_set: train dataset
    test_set: test dataset
    fitted: forecasted dataset
    confint: confidence interval of the forecast
    '''

    #train, test, split the data
    train_set = dataframe.loc[:cutoff]
    test_set = dataframe.loc[cutoff:end]

    # finding the best parameters of (p,d,q)x(P,D,Q)
    model = auto_arima(train_set[dest], 
                        start_p=0, start_q=0, d=0,
                        max_p=2, max_q=7, max_d=3,
                        start_P=0, start_Q=0, D=0,
                        max_P=2, max_Q=7, max_D=3,
                        m=12,
                        seasonal=True,
                        trace=False,
                        test='adf',
                        suppress_warnings=True,
                        stepwise=True,                      
                        )

    # forecast
    fitted, confint = model.predict(n_periods=periods, return_conf_int=True)

    return train_set, test_set, fitted, confint

We will begin with the SARIMA (baseline) model with the entire dataset inputted which will include the pandemic years. Most major airlines plan their flight schedule a year in advance; therefore, 1 year or 12 months will be forecasted for each destination. The test set will be a 12 month dataset to compare against the forecasted dataset. The results will be plotted for visual comparison.

In [60]:
# SARIMA with the entire dataset
df_fit=[]

for dest in df_main.columns:
    train, test, fit, ci = smodel(df_main, dest, 12, '2023-04-01')
    df_fit.append(fit)

    fig = px.line(train, x=train.index, y=dest)

    fig.add_trace(
        go.Scatter(x=test.index , y=test[dest], name='Test', mode='lines', line_color='orange'))

    fig.add_trace(
        go.Scatter(x=fit.index , y=fit, name='Forecast', mode='lines', line_color='crimson'))

    fig.add_trace(
        go.Scatter(x=fit.index, y=ci[:,[0]].flatten(), name='Confidence Interval', fill=None, mode='lines', line_color='lightgray'))

    fig.add_trace(
        go.Scatter(x=fit.index, y=ci[:,[1]].flatten(), name='Confidence Interval', fill='tonexty', mode='lines', line_color='lightgray'))

    fig.update_layout(
        title=f'Forecast of {dest}',
        yaxis_title='PASSENGERS',
        width=1600,
        height=300
    )
    fig.show()

df_fit = pd.concat(df_fit, axis=1)
df_fit.columns = [df_main.columns]

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(2,0,0)(1,0,1)[12] intercept (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(1,0,0)(2,0,1)[12] intercept (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(1,0,0)(2,0,1)[12]           (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(2,0,0)(2,0,2)[12]           (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

Inspecting the plots visually, although the confidence interval is wide for all the plots, surprisingly the SARIMA model did quite well forecasting for most of the destinations even with the anomaly in the data. Though the forecast may not be a perfect fit to the test data, for most of the destinations it followed the test data well and if anything under estimated the values.

Now let's see how well the SARIMA model does without the anomaly of the COVID impact in the data.

In [6]:
# pre-COVID forecast
df_fit1=[]

for dest1 in df_main.columns:
    train1, test1, fit1, ci1 = smodel(df_main,dest1,12,'2019-01-01','2020-01-01')
    df_fit1.append(fit1)

    fig1 = px.line(train1, x=train1.index, y=dest1)

    fig1.add_trace(
        go.Scatter(x=test1.index , y=test1[dest1], name='Test', mode='lines', line_color='orange'))

    fig1.add_trace(
        go.Scatter(x=fit1.index , y=fit1, name='Forecast', mode='lines', line_color='crimson'))

    fig1.add_trace(
        go.Scatter(x=fit1.index, y=ci1[:,[0]].flatten(), name='Confidence Interval', fill=None, mode='lines', line_color='lightgray'))

    fig1.add_trace(
        go.Scatter(x=fit1.index, y=ci1[:,[1]].flatten(), name='Confidence Interval', fill='tonexty', mode='lines', line_color='lightgray'))

    fig1.update_layout(
        title=f'Forecast of {dest1}',
        yaxis_title='PASSENGERS',
        width=1600,
        height=300
    )
    fig1.show()

df_fit1 = pd.concat(df_fit1, axis=1)
df_fit1.columns = [df_main.columns]

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(2,0,0)(1,0,0)[12]           (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(1,0,1)(1,0,1)[12]           (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py:524: ModelFitWarning:

Error fitting  ARIMA(2,0,0)(2,0,1)[12] intercept (if you do not want to see these warnings, run with error_action="ignore").
Traceback:
Traceback (most recent call last):
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\_auto_solvers.py", line 508, in _fit_candidate_model
    fit.fit(y, X=X, **fit_params)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 603, in fit
    self._fit(y, X, **fit_args)
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 524, in _fit
    fit, self.arima_res_ = _fit_wrapper()
                           ^^^^^^^^^^^^^^
  File "c:\Users\Joe\anaconda3\envs\capstone_joe_cha\Lib\site-packages\pmdarima\arima\arima.py", line 510, in _fit_wrapper
    fitted = arima.fit(
             ^^^^^^^^^^
  File "c:\Users\Joe\a

Again, inspecting the plots visually, the confidence interval is wide for all the plots and for most of the destinations the forecast seem to follow the test data better than the first model.

We will use two common performance metrics, Mean Absolute Error (MAE) and Mean Absolute Percentage Error (MAPE), to measure the accuracy of these SARIMA models.

### Evaluate SARIMA Models

In [7]:
# accuracy of SARIMA model with the entire dataset
from sklearn.metrics import mean_absolute_error, mean_absolute_percentage_error
mae_list = []
mape_list = []
for col in test.columns:
    test_pred = pd.merge(test[col], df_fit[col], left_index=True, right_index=True)
    test_pred.rename(columns={test_pred.columns[0]:'test', test_pred.columns[1]:'pred'}, inplace=True)

    y_true = test_pred['test']
    y_pred = test_pred['pred']

    mae = mean_absolute_error(y_true, y_pred)
    mae_list.append(mae)
    mape = mean_absolute_percentage_error(y_true, y_pred)
    mape_list.append(mape)


In [8]:
# combine the MAE and MAPE into one dataframe
df_mae = pd.DataFrame(mae_list, columns=['MAE'], index=test.columns)
df_mape = pd.DataFrame(mape_list, columns=['MAPE'], index=test.columns)
eval = pd.concat([df_mae, df_mape], axis=1)
eval

MAE      MAPE
London, United Kingdom  60055.616744  0.080978
Toronto, Canada         29062.202645  0.057405
Tokyo, Japan            37162.084284  0.109411
Cancun, Mexico          77265.584882  0.134621
Mexico City, Mexico     46094.885714  0.137193
...                              ...       ...
St. Lucia, Saint Lucia   4105.934392  0.188921
Lisbon, Portugal        20646.070987  0.267975
Cartagena, Colombia      8657.164929  0.337150
Morelia, Mexico          3701.398347  0.156165
Cali, Colombia           3530.473712  0.199490

[61 rows x 2 columns]

In [10]:
# statistical evaluation of MAE and MAPE
eval.describe()

MAE       MAPE
count     61.000000  61.000000
mean   18473.701338   0.263925
std    14162.158521   0.749300
min     1842.763320   0.043936
25%     9106.327693   0.114890
50%    14387.490855   0.154582
75%    23354.409069   0.204223
max    77265.584882   5.987120

In [11]:
# box plot to visualize the statistical evaluation of MAPE
fig_box=px.box(eval, y='MAPE',log_y=True)
fig_box.update_layout(
    width=400,
    height=600,
    title='MAPE'
)
fig_box.show()

For ease of interpretation, the MAPE is plotted on a boxplot. We can see there are a few outliers, with one huge outlier having a MAPE of 5.99 or 599%, meaning on average the forecasted number of passengers for that destination was 599% off from the actual (test) number of passengers each month. A destination had the best MAPE of 4.4% while most of the destinations had a MAPE of anywhere from 4.4% to 34%.

Now looking at the MAE and MAPE of the SARIMA model before the pandemic.

In [12]:
# accuracy of SARIMA model pre-COVID
mae_list1 = []
mape_list1 = []
for col in test1.columns:
    test_pred1 = pd.merge(test1[col], df_fit1[col], left_index=True, right_index=True)
    test_pred1.rename(columns={test_pred1.columns[0]:'test', test_pred1.columns[1]:'pred'}, inplace=True)

    y_true1 = test_pred1['test']
    y_pred1 = test_pred1['pred']

    mae1 = mean_absolute_error(y_true1, y_pred1)
    mae_list1.append(mae1)
    mape1 = mean_absolute_percentage_error(y_true1, y_pred1)
    mape_list1.append(mape1)

In [13]:
# combine the MAE and MAPE into one dataframe
df_mae1 = pd.DataFrame(mae_list1, columns=['MAE'], index=test1.columns)
df_mape1 = pd.DataFrame(mape_list1, columns=['MAPE'], index=test1.columns)
eval1 = pd.concat([df_mae1, df_mape1], axis=1)
eval1

MAE      MAPE
London, United Kingdom  54053.954309  0.062792
Toronto, Canada         29085.289509  0.045674
Tokyo, Japan            15855.090083  0.043701
Cancun, Mexico          22729.642485  0.070485
Mexico City, Mexico     17761.994469  0.046484
...                              ...       ...
St. Lucia, Saint Lucia   1848.456316  0.096218
Lisbon, Portugal        12512.286893  0.222467
Cartagena, Colombia      1044.875615  0.058191
Morelia, Mexico          2960.133219  0.168961
Cali, Colombia           3241.861534  0.278046

[61 rows x 2 columns]

In [14]:
# statistical evaluation of MAE and MAPE
eval1.describe()

MAE       MAPE
count     61.000000  61.000000
mean   11168.925941   0.120341
std     9478.588227   0.081686
min     1044.875615   0.026701
25%     4165.514623   0.067243
50%     8189.750424   0.096218
75%    14644.345718   0.160783
max    54053.954309   0.525090

In [15]:
# box plot to visualize the statistical evaluation of MAPE
fig_box1=px.box(eval1, y='MAPE',log_y=False)
fig_box1.update_layout(
    width=400,
    height=600,
    title='MAPE'
)
fig_box1.show()

Looking at the boxplot of the MAPE for the SARIMA model before COVID, it aligns with what we visually inspected that this model performed better. There is only one outlier with a MAPE of 53% which is a lot better than 599%. The lowest MAPE is 2.7% compared to 4.4% and for this model most of the destinations had a MAPE of anywhere from 2.7% to 29%. Given there is no major anomaly in the data, it's more plausible that the model trained on pre-COVID data would fare better than the model trained on post-COVID data.

As the goal of this project is to forecast the popular destinations based on flight history, we can look at if the forecasted destinations differ between the models.

In [16]:
# sample of the forecast results
df_fit.head()
forecast = df_fit.copy()

As done like in the EDA, the dataframe is reconfigured to produce the monthly top 10 destinations and plotted.

In [17]:
forecast = forecast.stack()

In [18]:
df_forecast = forecast.sum(axis=1).reset_index().\
    rename(columns={'level_0':'Date','level_1':'Destination',0:'Passengers'})

In [19]:
df_top=df_forecast.sort_values(by=['Date','Passengers'], ascending=[True,False]).reset_index(drop=True).\
    groupby(['Date']).apply(lambda x: x.head(10)).reset_index(drop=True)
df_top

Date             Destination     Passengers
0   2023-05-01  London, United Kingdom  833759.547867
1   2023-05-01         Toronto, Canada  547666.878937
2   2023-05-01          Cancun, Mexico  504068.039777
3   2023-05-01           Paris, France  362194.525907
4   2023-05-01     Mexico City, Mexico  315782.277676
..         ...                     ...            ...
115 2024-04-01     Mexico City, Mexico  251717.616253
116 2024-04-01      Seoul, South Korea  237405.921130
117 2024-04-01       Vancouver, Canada  230139.928946
118 2024-04-01  Amsterdam, Netherlands  227258.349438
119 2024-04-01      Frankfurt, Germany  211608.308009

[120 rows x 3 columns]

In [20]:
fig2 = px.line(
    df_top, x='Date', y='Passengers', color='Destination', facet_col='Destination',
    facet_col_wrap=5,
    height=600,
    width=2400,
    title='Popular Destinations'
              )
fig2.for_each_annotation(lambda x: x.update(text=x.text.split('=')[-1]))
fig2.show()

Interestingly, the popular destinations forecasted by the first model aligns with the top 10 destinations in terms of passenger volume. There looks to be a slight downwards trend or stagnation in these forecasts.

Let's see which destinations the second model before COVID forecasts.

In [21]:
# pre-COVID forecast
df_fit1.head()
forecast1 = df_fit1.copy()

In [22]:
forecast1 = forecast1.stack()
df_forecast1 = forecast1.sum(axis=1).reset_index().\
    rename(columns={'level_0':'Date','level_1':'Destination',0:'Passengers'})

In [23]:
df_top1=df_forecast1.sort_values(by=['Date','Passengers'], ascending=[True,False]).reset_index(drop=True).\
    groupby(['Date']).apply(lambda x: x.head(10)).reset_index(drop=True)

fig3 = px.line(
    df_top1, x='Date', y='Passengers', color='Destination', facet_col='Destination',
    facet_col_wrap=5,
    height=600,
    width=2400,
    title='Popular Destinations'
              )
fig3.for_each_annotation(lambda x: x.update(text=x.text.split('=')[-1]))
fig3.show()

Almost the same destinations but in different order and one instance of Montreal replacing Amsterdam and popping up in the top 10 at Feb 2019. The comparison of SARIMA models with the pandemic years included and excluded yielded some interesting results in terms of accuracy and destination forecasting. The model excluding the pandemic years had better accuracy of about 5% yet the forecasting of destinations were the same for both models. This could be interpreted as the model including the anomaly of pandemic years handled the anomaly quite well and with a 5% difference in accuracy was not large enough to affect the predictive power.

We now move onto advanced modeling using Meta (Facebook) Prophet model. Meta created this Prophet model specifically for forecasting time series models. It's a bit more complex than ARMA, ARIMA, or SARIMA models but not as complex as using neural networks such as Long Short-Term Memory (LSTM) or Gated Recurrent Unit (GRU) for time series models. It's a good balance between both.

### Advanced Modeling: Prophet

In [24]:
# import the libraries
from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly

One interesting feature the Prophet model has is the ability to include holidays or special events. This feature can be used to make the COVID lockdown period as a one time holiday/event that won't be repeated. The Prophet model will not capture the event(s) in its trend.

We will set the timeframe for the lockdown based on the longest cumulative lockdown which was about 9-10 months.

In [25]:
# set the COVID lockdown period as a one time event
lockdowns = pd.DataFrame([
    {'holiday': 'lockdown_1', 'ds': '2020-03-01', 'lower_window': 0, 'ds_upper': '2021-01-01'} # COVID lockdown began in March 2020 for US. Longest COVID lockdown was about 9-10 months.
])
for t_col in ['ds', 'ds_upper']:
    lockdowns[t_col] = pd.to_datetime(lockdowns[t_col])
lockdowns['upper_window'] = (lockdowns['ds_upper'] - lockdowns['ds']).dt.days
lockdowns

holiday         ds  lower_window   ds_upper  upper_window
0  lockdown_1 2020-03-01             0 2021-01-01           306

A custom function `pmodel` is created to automate the steps for setting up the `Prophet` model in order to iterate through the destinations.

In [26]:
def pmodel(city, dataframe, period, cutoff, holiday=None):
    '''
    Description
    -----------
    Given a time series dataframe, the dataset will be split for train set and test set.
    Prophet model requires specific column names and so the date column will be renamed to ds and destination column to y.
    The data will be fitted to the Prophet model and predicted.
    The results will be plotted for visual analysis.

    Inputs
    ------
    city: name of destination
    dataframe: dataframe of the time series data
    period: timeframe to forecast
    cutoff: cutoff date for the train test split
    holiday (optional): holiday or special events for the Prophet model to take into account

    Outputs
    forecasts: forecasted dataset
    date: dates of the forecasted data
    test_df: test dataset
    ------

    '''
    # train test split
    train_df = dataframe[:cutoff].reset_index()
    test_df = dataframe[cutoff:]

    # rename the columns to meet the requirements
    prophet_df = pd.concat([train_df['DATE'], train_df[city]], axis=1)
    prophet_df.rename(columns={'DATE': 'ds', city:'y'}, inplace=True)

    # instantiate and fit
    model = Prophet(holidays=holiday, yearly_seasonality=True)
    model.fit(prophet_df)

    # create the dataframe for forecast data
    future = model.make_future_dataframe(periods=period, freq='MS', include_history=False)
    
    # forecast and insert the data into the dataframe
    forecast = model.predict(future)
    
    # plot the results
    fig = plot_plotly(model, forecast, xlabel='Date', ylabel='Passengers')
    fig.update_layout(title=f'{city}')
    fig.show()

    # extract the forecast data and dates
    forecasts = forecast[['yhat']].rename(columns={'yhat':city})
    date = forecast[['ds']]
      
    return forecasts, date, test_df

As done with the baseline modeling, we will look at the advanced modeling with the entire dataset first.

In [27]:
# Prophet model with the entire dataset
forecast_list = []
for cityname in df_main.columns:
    forecasts, date, testset = pmodel(cityname, df_main, 12, '2023-04-01', lockdowns)
    forecast_list.append(forecasts)

forecast_df = pd.concat(forecast_list, axis=1)
prophet_df = pd.concat([date, forecast_df], axis=1).set_index('ds')

16:08:43 - cmdstanpy - INFO - Chain [1] start processing
16:08:43 - cmdstanpy - INFO - Chain [1] done processing


16:08:44 - cmdstanpy - INFO - Chain [1] start processing
16:08:44 - cmdstanpy - INFO - Chain [1] done processing


16:08:44 - cmdstanpy - INFO - Chain [1] start processing
16:08:44 - cmdstanpy - INFO - Chain [1] done processing


16:08:44 - cmdstanpy - INFO - Chain [1] start processing
16:08:44 - cmdstanpy - INFO - Chain [1] done processing


16:08:45 - cmdstanpy - INFO - Chain [1] start processing
16:08:45 - cmdstanpy - INFO - Chain [1] done processing


...

16:09:07 - cmdstanpy - INFO - Chain [1] start processing
16:09:07 - cmdstanpy - INFO - Chain [1] done processing


16:09:07 - cmdstanpy - INFO - Chain [1] start processing
16:09:07 - cmdstanpy - INFO - Chain [1] done processing


16:09:07 - cmdstanpy - INFO - Chain [1] start processing
16:09:08 - cmdstanpy - INFO - Chain [1] done processing


16:09:08 - cmdstanpy - INFO - Chain [1] start processing
16:09:08 - cmdstanpy - INFO - Chain [1] done processing


16:09:08 - cmdstanpy - INFO - Chain [1] start processing
16:09:08 - cmdstanpy - INFO - Chain [1] done processing


Unfortunately, `plot_plotly` does not have the option to include the test dataset so we cannot visually compare the forecast against the test dataset. However, it does plot the confidence interval we saw before in the baseline models plots. The Prophet model has a narrower band of confidence interval than the SARIMA models and even for some destinations the confidence interval is slim. MAE and MAPE will tell us better how well the model did in its predictions.

Before evaluation the performance of this Prophet model, we will look at the Prophet model before the pandemic years.

In [36]:
# pre-COVID
forecast_list1 = []
for cityname1 in df_main.columns:
    forecasts1, date1, testset1 = pmodel(cityname1, df_main, 12, '2019-01-01')
    forecast_list1.append(forecasts1)
    
forecast_df1 = pd.concat(forecast_list1, axis=1)
prophet_df1 = pd.concat([date1, forecast_df1], axis=1).set_index('ds')

16:09:09 - cmdstanpy - INFO - Chain [1] start processing
16:09:10 - cmdstanpy - INFO - Chain [1] done processing


16:09:10 - cmdstanpy - INFO - Chain [1] start processing
16:09:10 - cmdstanpy - INFO - Chain [1] done processing


16:09:11 - cmdstanpy - INFO - Chain [1] start processing
16:09:11 - cmdstanpy - INFO - Chain [1] done processing


16:09:11 - cmdstanpy - INFO - Chain [1] start processing
16:09:11 - cmdstanpy - INFO - Chain [1] done processing


16:09:12 - cmdstanpy - INFO - Chain [1] start processing
16:09:12 - cmdstanpy - INFO - Chain [1] done processing


...

16:09:39 - cmdstanpy - INFO - Chain [1] start processing
16:09:40 - cmdstanpy - INFO - Chain [1] done processing


16:09:40 - cmdstanpy - INFO - Chain [1] start processing
16:09:41 - cmdstanpy - INFO - Chain [1] done processing


16:09:41 - cmdstanpy - INFO - Chain [1] start processing
16:09:41 - cmdstanpy - INFO - Chain [1] done processing


16:09:42 - cmdstanpy - INFO - Chain [1] start processing
16:09:42 - cmdstanpy - INFO - Chain [1] done processing


16:09:42 - cmdstanpy - INFO - Chain [1] start processing
16:09:42 - cmdstanpy - INFO - Chain [1] done processing


Similarly to the SARIMA model pre-COVID, the Prophet model before the pandemic years seem to perform better than its predecessor model from visual inspection. The confidence interval is narrower for a lot of the destinations, some even fitting to the forecast data.

We will take a look at MAE and MAPE for the Prophet models to see which one did perform better.

### Evaluate Prophet Models

In [ ]:
# Prophet model with the entire dataset
from sklearn.metrics import mean_absolute_error, mean_absolute_percentage_error
p_mae_list = []
p_mape_list = []
for p_col in testset.columns:
    p_test_pred = pd.merge(testset[p_col], prophet_df[p_col], left_index=True, right_index=True)
    p_test_pred.rename(columns={p_test_pred.columns[0]:'test', p_test_pred.columns[1]:'pred'}, inplace=True)

    p_true = p_test_pred['test']
    p_pred = p_test_pred['pred']

    p_mae = mean_absolute_error(p_true, p_pred)
    p_mae_list.append(p_mae)
    p_mape = mean_absolute_percentage_error(p_true, p_pred)
    p_mape_list.append(p_mape)


In [ ]:
p_mae_df = pd.DataFrame(p_mae_list, columns=['MAE'], index=testset.columns)
p_mape_df = pd.DataFrame(p_mape_list, columns=['MAPE'], index=testset.columns)
p_eval = pd.concat([p_mae_df, p_mape_df], axis=1)

In [ ]:
p_eval

MAE      MAPE
London, United Kingdom  275601.222940  0.349972
Toronto, Canada         146160.947126  0.278807
Tokyo, Japan            203062.617807  0.611713
Cancun, Mexico           34940.553422  0.071579
Mexico City, Mexico      46307.352054  0.138800
...                               ...       ...
St. Lucia, Saint Lucia    2274.540186  0.112799
Lisbon, Portugal         19316.948045  0.247122
Cartagena, Colombia       6027.066156  0.233916
Morelia, Mexico            787.638825  0.033298
Cali, Colombia            4108.858589  0.343049

[61 rows x 2 columns]

In [ ]:
p_eval.describe()

MAE       MAPE
count      61.000000  61.000000
mean    34990.945516   0.251632
std     48865.985022   0.212015
min       787.638825   0.021481
25%      6182.488046   0.131389
50%     20177.135738   0.231267
75%     35508.785702   0.310402
max    275601.222940   1.545404

In [ ]:
fig_box2=px.box(p_eval, y='MAPE',log_y=True)
fig_box2.update_layout(
    width=400,
    height=600,
    title='MAPE'
)
fig_box2.show()

The boxplot shows a few outliers with the maximum MAPE being 155%. The lowest MAPE for this model is 2.1% and most of the destinations had a MAPE of anywhere between 2.1% and 46%.

Now looking at the MAE and MAPE for the Prophet model before the pandemic years.

In [ ]:
# Prophet model before COVID
p_mae_list1 = []
p_mape_list1 = []
for p_col1 in testset1.columns:
    p_test_pred1 = pd.merge(testset1[p_col1], prophet_df1[p_col1], left_index=True, right_index=True)
    p_test_pred1.rename(columns={p_test_pred1.columns[0]:'test', p_test_pred1.columns[1]:'pred'}, inplace=True)

    p_true1 = p_test_pred1['test']
    p_pred1 = p_test_pred1['pred']

    p_mae1 = mean_absolute_error(p_true1, p_pred1)
    p_mae_list1.append(p_mae1)
    p_mape1 = mean_absolute_percentage_error(p_true1, p_pred1)
    p_mape_list1.append(p_mape1)


In [ ]:
p_mae_df1 = pd.DataFrame(p_mae_list1, columns=['MAE'], index=testset1.columns)
p_mape_df1 = pd.DataFrame(p_mape_list1, columns=['MAPE'], index=testset1.columns)
p_eval1 = pd.concat([p_mae_df1, p_mape_df1], axis=1)

In [ ]:
p_eval1

MAE      MAPE
London, United Kingdom  31514.941947  0.040539
Toronto, Canada         28847.644260  0.050086
Tokyo, Japan            21233.015757  0.055779
Cancun, Mexico          17757.810760  0.056413
Mexico City, Mexico     40551.613239  0.120416
...                              ...       ...
St. Lucia, Saint Lucia   1206.247037  0.060019
Lisbon, Portugal         5125.475798  0.104642
Cartagena, Colombia      1752.261213  0.102413
Morelia, Mexico           936.866132  0.050066
Cali, Colombia           3102.167499  0.272107

[61 rows x 2 columns]

In [ ]:
p_eval1.describe()

MAE       MAPE
count     61.000000  61.000000
mean    8644.743987   0.104005
std     7936.649259   0.102812
min      936.866132   0.031686
25%     3102.167499   0.050231
50%     5752.644176   0.073794
75%    11255.394683   0.104642
max    40551.613239   0.574346

In [ ]:
fig_box3=px.box(p_eval1, y='MAPE',log_y=True)
fig_box3.update_layout(
    width=400,
    height=600,
    title='MAPE'
)
fig_box3.show()

Surprisingly, this model had more outliers with the maximum MAPE being 574%! The lowest MAPE is 3.2% compared to 2.1%. Most of the destinations for this model had a MAPE of anywhere between 3.2% and 18% which is better than the 2.1% to 46% range. <br>
It's a bit difficult to concretely state that this Prophet model is better than the other Prophet model since this model had a lower range of MAPE it had quite a lot more outliers. However, we do need to take into account that the Prophet model with the pandemic years did not capture the lockdown period thanks to the holiday feature. So for the given accuracy scores, that model did well for capturing the irregularities of the recovery period from the pandemic shock and predicting nearly as well as this model with no anomalies.

For the final steps of the Prophet models, we will look at the forecasted popular destinations.

In [ ]:
# Prophet model with the entire dataset
prophet_forecast = prophet_df.stack()
prophet_forecast = pd.DataFrame(prophet_forecast)

In [ ]:
df_prophet = prophet_forecast.sum(axis=1).reset_index().\
    rename(columns={'ds':'Date','level_1':'Destination',0:'Passengers'})

In [ ]:
df_top_prophet=df_prophet.sort_values(by=['Date','Passengers'], ascending=[True,False]).reset_index(drop=True).\
    groupby(['Date']).apply(lambda x: x.head(10)).reset_index(drop=True)

fig4 = px.line(
    df_top_prophet, x='Date', y='Passengers', color='Destination', facet_col='Destination',
    facet_col_wrap=5,
    height=600,
    width=2400,
    title='Popular Destinations'
              )
fig4.for_each_annotation(lambda x: x.update(text=x.text.split('=')[-1]))
fig4.show()

The Prophet model with the entire dataset seemed to have a variety of forecasts. There are familiar destinations as before and a few new ones. There's also mix of upward, downward, and stagnant trends. Destinations such as Tokyo and Seoul that were deemed to be in the monthly top 10 constantly by the SARIMA model make it to the top 10 a few times for this Prophet model.

Let's see what the Prophet model before the pandemic years forecasted.

In [37]:
# Prophet model before COVID
prophet_forecast1 = prophet_df1.stack()
prophet_forecast1 = pd.DataFrame(prophet_forecast1)

In [38]:
df_prophet1 = prophet_forecast1.sum(axis=1).reset_index().\
    rename(columns={'ds':'Date','level_1':'Destination',0:'Passengers'})

In [39]:
df_top_prophet1=df_prophet1.sort_values(by=['Date','Passengers'], ascending=[True,False]).reset_index(drop=True).\
    groupby(['Date']).apply(lambda x: x.head(10)).reset_index(drop=True)

fig5 = px.line(
    df_top_prophet1, x='Date', y='Passengers', color='Destination', facet_col='Destination',
    facet_col_wrap=5,
    height=600,
    width=2400,
    title='Popular Destinations'
              )
fig5.for_each_annotation(lambda x: x.update(text=x.text.split('=')[-1]))
fig5.show()

Interestingly, the forecast of this Prophet model before the pandemic years differ and align closer to the baseline model forecasts.

### Final Conclusion / Findings

Summary of the accuracies of the models:
- SARIMA w/ pandemic years: 4.4-34%
- SARIMA w/out pandemic years: 2.7-29%
- Prophet w/ pandemic years: 2.1-46%
- Prophet w/out pandemic years: 3.2-18%

For both the SARIMA and Prophet models, the models trained on dataset before 2020 yielded better MAPE. All the models forecasted the same popular destinations except for the Prophet model with pandemic years where it forecasted additional destinations. Looking at this model evaluations, the main question is whether to include or exclude major anomalies in data such as COVID lockdown for the aviation industry. 3 of the 4 models came to the same conclusion and one provided the same conclusion plus more. Some interesting or important interpretations could be derived from the odd one out. Perhaps other parameters for the Prophet model could be looked into or expand the top 10 destinations to top 50 and compare those results.<br>
Whichever the case may be, all the models were reasonably similar in their performance metric but perhaps the Prophet model with additional destinations should be utilized to capture all the possibilities.